In [19]:
# 🛠️ Step 1: Install required libraries quietly
!pip install evaluate transformers datasets tokenizers seqeval pandas pyarrow -q

# 🚫 Step 2: Disable Weights & Biases (WandB)
import os
os.environ["WANDB_MODE"] = "disabled"

# 📚 Step 2: Import necessary libraries
import pandas as pd
import datasets
import numpy as np
from transformers import BertTokenizerFast
from transformers import DataCollatorForTokenClassification
from transformers import AutoModelForTokenClassification
from transformers import TrainingArguments, Trainer
import evaluate
from transformers import pipeline
from collections import defaultdict
import json

# 📥 Step 3: Load the CoNLL-2025 NER dataset from Parquet
# Download : https://huggingface.co/datasets/boltuix/conll2025-ner/blob/main/conll2025_ner.parquet
parquet_file = "conll2025_ner.parquet"
df = pd.read_parquet(parquet_file)

# 🔍 Step 4: Convert pandas DataFrame to Hugging Face Dataset
conll2025 = datasets.Dataset.from_pandas(df)

# 🔎 Step 5: Inspect the dataset structure
print("Dataset structure:", conll2025)
print("Dataset features:", conll2025.features)
print("First example:", conll2025[0])

# 🏷️ Step 6: Extract unique tags and create mappings
# Since ner_tags are strings, collect all unique tags
all_tags = set()
for example in conll2025:
    all_tags.update(example["ner_tags"])
unique_tags = sorted(list(all_tags))  # Sort for consistency
num_tags = len(unique_tags)
tag2id = {tag: i for i, tag in enumerate(unique_tags)}
id2tag = {i: tag for i, tag in enumerate(unique_tags)}
print("Number of unique tags:", num_tags)
print("Unique tags:", unique_tags)

# 🔧 Step 7: Convert string ner_tags to indices
def convert_tags_to_ids(example):
    example["ner_tags"] = [tag2id[tag] for tag in example["ner_tags"]]
    return example

conll2025 = conll2025.map(convert_tags_to_ids)

# 📊 Step 8: Split dataset based on 'split' column
dataset_dict = {
    "train": conll2025.filter(lambda x: x["split"] == "train"),
    "validation": conll2025.filter(lambda x: x["split"] == "validation"),
    "test": conll2025.filter(lambda x: x["split"] == "test")
}
conll2025 = datasets.DatasetDict(dataset_dict)
print("Split dataset structure:", conll2025)

# 🪙 Step 9: Initialize the tokenizer
tokenizer = BertTokenizerFast.from_pretrained("boltuix/bert-mini")

# 📝 Step 10: Tokenize an example text and inspect
example_text = conll2025["train"][0]
tokenized_input = tokenizer(example_text["tokens"], is_split_into_words=True)
tokens = tokenizer.convert_ids_to_tokens(tokenized_input["input_ids"])
word_ids = tokenized_input.word_ids()
print("Word IDs:", word_ids)
print("Tokenized input:", tokenized_input)
print("Length of ner_tags vs input IDs:", len(example_text["ner_tags"]), len(tokenized_input["input_ids"]))

# 🔄 Step 11: Define function to tokenize and align labels
def tokenize_and_align_labels(examples, label_all_tokens=True):
    """
    Tokenize inputs and align labels for NER tasks.

    Args:
        examples (dict): Dictionary with tokens and ner_tags.
        label_all_tokens (bool): Whether to label all subword tokens.

    Returns:
        dict: Tokenized inputs with aligned labels.
    """
    tokenized_inputs = tokenizer(examples["tokens"], truncation=True, is_split_into_words=True)
    labels = []
    for i, label in enumerate(examples["ner_tags"]):
        word_ids = tokenized_inputs.word_ids(batch_index=i)
        previous_word_idx = None
        label_ids = []
        for word_idx in word_ids:
            if word_idx is None:
                label_ids.append(-100)  # Special tokens get -100
            elif word_idx != previous_word_idx:
                label_ids.append(label[word_idx])  # First token of word gets label
            else:
                label_ids.append(label[word_idx] if label_all_tokens else -100)  # Subwords get label or -100
            previous_word_idx = word_idx
        labels.append(label_ids)
    tokenized_inputs["labels"] = labels
    return tokenized_inputs

# 🧪 Step 12: Test the tokenization and label alignment
q = tokenize_and_align_labels(conll2025["train"][0:1])
print("Tokenized and aligned example:", q)

# 📋 Step 13: Print tokens and their corresponding labels
for token, label in zip(tokenizer.convert_ids_to_tokens(q["input_ids"][0]), q["labels"][0]):
    print(f"{token:_<40} {label}")

# 🔧 Step 14: Apply tokenization to the entire dataset
tokenized_datasets = conll2025.map(tokenize_and_align_labels, batched=True)

# 🤖 Step 15: Initialize the model with the correct number of labels
model = AutoModelForTokenClassification.from_pretrained("boltuix/bert-mini", num_labels=num_tags)

# ⚙️ Step 16: Set up training arguments
args = TrainingArguments(
    "boltuix/bert-ner",
    eval_strategy="epoch", # Changed evaluation_strategy to eval_strategy
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=1,
    weight_decay=0.01,
    report_to="none"
)
# 📊 Step 17: Initialize data collator for dynamic padding
data_collator = DataCollatorForTokenClassification(tokenizer)

# 📈 Step 18: Load evaluation metric
metric = evaluate.load("seqeval")

# 🏷️ Step 19: Set label list and test metric computation
label_list = unique_tags
print("Label list:", label_list)
example = conll2025["train"][0]
labels = [label_list[i] for i in example["ner_tags"]]
print("Metric test:", metric.compute(predictions=[labels], references=[labels]))

# 📉 Step 20: Define function to compute evaluation metrics
def compute_metrics(eval_preds):
    """
    Compute precision, recall, F1, and accuracy for NER.

    Args:
        eval_preds (tuple): Predicted logits and true labels.

    Returns:
        dict: Evaluation metrics.
    """
    pred_logits, labels = eval_preds
    pred_logits = np.argmax(pred_logits, axis=2)
    predictions = [
        [label_list[p] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(pred_logits, labels)
    ]
    true_labels = [
        [label_list[l] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(pred_logits, labels)
    ]
    results = metric.compute(predictions=predictions, references=true_labels)
    return {
        "precision": results["overall_precision"],
        "recall": results["overall_recall"],
        "f1": results["overall_f1"],
        "accuracy": results["overall_accuracy"],
    }

# 🚀 Step 21: Initialize and train the trainer
trainer = Trainer(
    model,
    args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["validation"],
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)
trainer.train()

# 💾 Step 22: Save the fine-tuned model
model.save_pretrained("boltuix/bert-ner")
tokenizer.save_pretrained("tokenizer")

# 🔗 Step 23: Update model configuration with label mappings
id2label = {str(i): label for i, label in enumerate(label_list)}
label2id = {label: str(i) for i, label in enumerate(label_list)}
config = json.load(open("boltuix/bert-ner/config.json"))
config["id2label"] = id2label
config["label2id"] = label2id
json.dump(config, open("boltuix/bert-ner/config.json", "w"))

# 🔄 Step 24: Load the fine-tuned model
model_fine_tuned = AutoModelForTokenClassification.from_pretrained("boltuix/bert-ner")

# 🛠️ Step 25: Create a pipeline for NER inference
nlp = pipeline("token-classification", model=model_fine_tuned, tokenizer=tokenizer)

# 📝 Step 26: Perform NER on an example sentence
example = "On July 4th, 2023, President Joe Biden visited the United Nations headquarters in New York to deliver a speech about international law and donated $5 million to relief efforts."
ner_results = nlp(example)
print("NER results for first example:", ner_results)

# 📍 Step 27: Perform NER on a property address and format output
example = "This page contains information about the property located at 1275 Kinnear Rd, Columbus, OH, 43212."
ner_results = nlp(example)

# 🧹 Step 28: Process NER results into structured entities
entities = defaultdict(list)
current_entity = ""
current_type = ""

for item in ner_results:
    entity = item["entity"]
    word = item["word"]
    if word.startswith("##"):
        current_entity += word[2:]  # Handle subword tokens
    elif entity.startswith("B-"):
        if current_entity and current_type:
            entities[current_type].append(current_entity.strip())
        current_type = entity[2:].lower()
        current_entity = word
    elif entity.startswith("I-") and entity[2:].lower() == current_type:
        current_entity += " " + word  # Continue same entity
    else:
        if current_entity and current_type:
            entities[current_type].append(current_entity.strip())
        current_entity = ""
        current_type = ""

# Append final entity if exists
if current_entity and current_type:
    entities[current_type].append(current_entity.strip())

# 📤 Step 29: Output the final JSON
final_json = dict(entities)
print("Structured NER output:")
print(json.dumps(final_json, indent=2))


Dataset structure: Dataset({
    features: ['split', 'tokens', 'ner_tags'],
    num_rows: 143709
})
Dataset features: {'split': Value(dtype='string', id=None), 'tokens': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None), 'ner_tags': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None)}
First example: {'split': 'train', 'tokens': ['Big', 'Managers', 'on', 'Campus'], 'ner_tags': ['O', 'O', 'O', 'O']}
Number of unique tags: 37
Unique tags: ['B-CARDINAL', 'B-DATE', 'B-EVENT', 'B-FAC', 'B-GPE', 'B-LANGUAGE', 'B-LAW', 'B-LOC', 'B-MONEY', 'B-NORP', 'B-ORDINAL', 'B-ORG', 'B-PERCENT', 'B-PERSON', 'B-PRODUCT', 'B-QUANTITY', 'B-TIME', 'B-WORK_OF_ART', 'I-CARDINAL', 'I-DATE', 'I-EVENT', 'I-FAC', 'I-GPE', 'I-LANGUAGE', 'I-LAW', 'I-LOC', 'I-MONEY', 'I-NORP', 'I-ORDINAL', 'I-ORG', 'I-PERCENT', 'I-PERSON', 'I-PRODUCT', 'I-QUANTITY', 'I-TIME', 'I-WORK_OF_ART', 'O']


Map:   0%|          | 0/143709 [00:00<?, ? examples/s]

Filter:   0%|          | 0/143709 [00:00<?, ? examples/s]

Filter:   0%|          | 0/143709 [00:00<?, ? examples/s]

Filter:   0%|          | 0/143709 [00:00<?, ? examples/s]

...

Some weights of BertForTokenClassification were not initialized from the model checkpoint at boltuix/bert-mini and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Label list: ['B-CARDINAL', 'B-DATE', 'B-EVENT', 'B-FAC', 'B-GPE', 'B-LANGUAGE', 'B-LAW', 'B-LOC', 'B-MONEY', 'B-NORP', 'B-ORDINAL', 'B-ORG', 'B-PERCENT', 'B-PERSON', 'B-PRODUCT', 'B-QUANTITY', 'B-TIME', 'B-WORK_OF_ART', 'I-CARDINAL', 'I-DATE', 'I-EVENT', 'I-FAC', 'I-GPE', 'I-LANGUAGE', 'I-LAW', 'I-LOC', 'I-MONEY', 'I-NORP', 'I-ORDINAL', 'I-ORG', 'I-PERCENT', 'I-PERSON', 'I-PRODUCT', 'I-QUANTITY', 'I-TIME', 'I-WORK_OF_ART', 'O']
Metric test: {'overall_precision': np.float64(0.0), 'overall_recall': np.float64(0.0), 'overall_f1': np.float64(0.0), 'overall_accuracy': 1.0}


/usr/local/lib/python3.11/dist-packages/seqeval/metrics/v1.py:57: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.11/dist-packages/seqeval/metrics/v1.py:57: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.11/dist-packages/numpy/lib/_function_base_impl.py:557: RuntimeWarning: Mean of empty slice.
  avg = a.mean(axis, **keepdims_kw)
/usr/local/lib/python3.11/dist-packages/numpy/_core/_methods.py:138: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
<ipython-input-19-599946481>:172: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 fo

/usr/local/lib/python3.11/dist-packages/seqeval/metrics/v1.py:57: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
Device set to use cuda:0


NER results for first example: [{'entity': 'B-DATE', 'score': np.float32(0.4680284), 'index': 2, 'word': 'july', 'start': 3, 'end': 7}, {'entity': 'B-DATE', 'score': np.float32(0.40818664), 'index': 3, 'word': '4th', 'start': 8, 'end': 11}, {'entity': 'B-DATE', 'score': np.float32(0.27342722), 'index': 5, 'word': '202', 'start': 13, 'end': 16}, {'entity': 'I-DATE', 'score': np.float32(0.24528159), 'index': 6, 'word': '##3', 'start': 16, 'end': 17}, {'entity': 'B-PERSON', 'score': np.float32(0.5311531), 'index': 9, 'word': 'joe', 'start': 29, 'end': 32}, {'entity': 'I-PERSON', 'score': np.float32(0.475913), 'index': 10, 'word': 'bid', 'start': 33, 'end': 36}, {'entity': 'I-PERSON', 'score': np.float32(0.40657172), 'index': 11, 'word': '##en', 'start': 36, 'end': 38}, {'entity': 'B-ORG', 'score': np.float32(0.26126653), 'index': 13, 'word': 'the', 'start': 47, 'end': 50}, {'entity': 'B-ORG', 'score': np.float32(0.22172953), 'index': 14, 'word': 'united', 'start': 51, 'end': 57}, {'entity